In [0]:
!pip install pyspark

     |████████████████████████████████| 215.7MB 74kB/s 
     |████████████████████████████████| 204kB 48.8MB/s 
  Created wheel for pyspark: filename=pyspark-2.4.4-py2.py3-none-any.whl size=216130387 sha256=923f50a38a93ad499606badce43a4bd6d982402c513fdbcacf5e2adb8150eb19
  Stored in directory: /root/.cache/pip/wheels/ab/09/4d/0d184230058e654eb1b04467dbc1292f00eaa186544604b471
Successfully built pyspark


In [0]:
import urllib.request, json
import requests

from pyspark import *
from pyspark.sql import SQLContext
from pyspark.sql.types import *
from pyspark.sql.functions import udf

import time
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sb

In [0]:
conf = SparkConf()
conf = (conf.setMaster('local[*]')
        .set('spark.executor.memory', '10G')
        .set('spark.driver.memory', '10G')
        .set('spark.driver.maxResultSize', '10G')
        .set('spark.sql.shuffle.partitions', '800'))
sc = SparkContext(conf = conf, master="local", appName="MtgAnalyse")
sc

<SparkContext master=local appName=MtgAnalyse>

In [0]:
#sc.stop()

In [138]:
from google.colab import files

### On importe AllCards.json
AllCardFile = files.upload()

In [0]:
!ls /content 
!pwd

AllCards.json  sample_data
/content


In [0]:
AllCardsSqlContext = SQLContext (sc)
#AllCardsPdDf = pd.read_json (io.BytesIO(AllCardFile["AllCards.json"]), orient='index')
AllCardsDf  = AllCardsSqlContext.read.json ("/content/AllCards.json")

Py4JJavaError: ignored

In [0]:
url = "https://www.mtgjson.com/files/AllCards.json"
headers = {'User-Agent': 'Mozilla/5.0 (Windows; U; Windows NT 5.1; en-US; rv:1.9.0.7) Gecko/2009021910 Firefox/3.0.7'}

request = urllib.request.Request(url, None, headers)
response = urllib.request.urlopen(request)
data = json.loads(response.read())

In [0]:
data

{'"Ach! Hans, Run!"': {'colorIdentity': ['G', 'R'],
  'colors': ['G', 'R'],
  'convertedManaCost': 6.0,
  'foreignData': [],
  'layout': 'normal',
  'legalities': {},
  'manaCost': '{2}{R}{R}{G}{G}',
  'name': '"Ach! Hans, Run!"',
  'printings': ['UNH'],
  'purchaseUrls': {'cardmarket': 'https://mtgjson.com/links/6227e6c981cce27c',
   'tcgplayer': 'https://mtgjson.com/links/85b366724beadefd'},
  'rulings': [],
  'scryfallOracleId': 'a2c5ee76-6084-413c-bb70-45490d818374',
  'subtypes': [],
  'supertypes': [],
  'text': 'At the beginning of your upkeep, you may say "Ach Hans, run It\'s the . . ." and the name of a creature card. If you do, search your library for a card with that name, put it onto the battlefield, then shuffle your library. That creature gains haste. Exile it at the beginning of the next end step.',
  'type': 'Enchantment',
  'types': ['Enchantment'],
  'uuid': '8f9a35d5-a3a2-556b-88da-6686da3aaa34'},
 '"Rumors of My Death . . ."': {'colorIdentity': ['B'],
  'colors': ['

In [0]:
#
#
### A bit of pandas
#
#

In [0]:
AllCardsPdDf = pd.read_json (io.BytesIO(AllCardFile["AllCards.json"]), orient='index')

In [154]:
AllCardsPdDf

colorIdentity  ...                                  uuid
"Ach! Hans, Run!"                    [G, R]  ...  8f9a35d5-a3a2-556b-88da-6686da3aaa34
"Rumors of My Death . . ."              [B]  ...  201f7042-dda1-53d6-a0bd-8225ba73f34a
1996 World Champion         [B, G, R, U, W]  ...  6b0e48c0-441d-5a62-a558-3c99473e4387
A Display of My Dark Power               []  ...  5ccf5ac6-84e6-5ae8-a801-6e9cac2f1996
A Good Thing                         [B, W]  ...  5e77de09-7521-54b6-b516-b7ed7740f7fe
...                                     ...  ...                                   ...
Zurgo Helmsmasher                 [B, R, W]  ...  95affd9d-36c6-521b-a44a-09975c2c1a6d
Zyym, Mesmeric Lord                  [B, U]  ...  0b6a65a0-69fd-59f7-8186-9e4c507343a8
Zzzyxas's Abyss                         [B]  ...  d55dfa2f-5c3f-5070-8791-72aab11793b8
_____                                   [U]  ...  71dbd495-fc0f-5539-8373-5e0bc02977f6
capital offense                         [B]  ...  d850e5bd-592c-548b-8602-9d5735a1b6d9

[20730 rows x 37 columns]

In [0]:
dj = pd.read_json('AllCards.json', orient='index')
for col in dj.columns.to_list():
  if dj[col].dtypes == 'object': 
    dj[col] = dj[col].astype(str)
AllCardsDj = AllCardsSqlContext.createDataFrame(dj)

In [0]:
AllCardsDj.show(10)

+--------------------+--------------+--------------------+-----------------+----------+---------------------+--------------------+----+--------------+---------+-------------+----------+------+----------------+--------------------+----+-------+---------------+----------+----------+-------+--------------------+-----+------------+-----+---------+--------------------+--------------------+--------------------+----+----------+----------+--------------------+---------+---------------+---------------+--------------------+
|       colorIdentity|colorIndicator|              colors|convertedManaCost|edhrecRank|faceConvertedManaCost|         foreignData|hand|hasNoDeckLimit|isBuyABox|isDateStamped|isReserved|layout|leadershipSkills|          legalities|life|loyalty|       manaCost|mtgArenaId|mtgoFoilId| mtgoId|                name|names|otherFaceIds|power|printings|        purchaseUrls|             rulings|    scryfallOracleId|side|  subtypes|supertypes|                text|toughness|           typ

In [124]:
#Voyons si une couleur est favorisé
AllCardsDj.createOrReplaceTempView('AllCards')
proto = AllCardsSqlContext.sql("SELECT count(colorIdentity) as NB, colorIdentity FROM AllCards GROUP BY colorIdentity")
proto.show(truncate = False)

+----+-------------------------+
|NB  |colorIdentity            |
+----+-------------------------+
|210 |['B', 'G']               |
|200 |['R', 'W']               |
|292 |['B', 'R']               |
|3126|['B']                    |
|3104|['R']                    |
|30  |['B', 'G', 'U']          |
|287 |['U', 'W']               |
|292 |['B', 'U']               |
|25  |['B', 'G', 'W']          |
|2289|[]                       |
|2   |['B', 'R', 'U', 'W']     |
|58  |['B', 'G', 'R']          |
|24  |['G', 'R', 'U']          |
|2   |['G', 'R', 'U', 'W']     |
|3086|['U']                    |
|289 |['G', 'W']               |
|68  |['B', 'G', 'R', 'U', 'W']|
|31  |['B', 'R', 'W']          |
|3098|['W']                    |
|3   |['B', 'G', 'U', 'W']     |
+----+-------------------------+
only showing top 20 rows



In [169]:
proto = AllCardsSqlContext.sql("SELECT name FROM AllCards WHERE colorIdentity = \"['U']\"")
proto.show(truncate = False)

+-------------------------+
|name                     |
+-------------------------+
|Abduction                |
|Aberrant Researcher      |
|Abjure                   |
|Aboshan's Desire         |
|Aboshan, Cephalid Emperor|
|Abstruse Interference    |
|Academy Drake            |
|Academy Elite            |
|Academy Journeymage      |
|Academy Researchers      |
|Academy Ruins            |
|Accumulated Knowledge    |
|Acid Rain                |
|Acquire                  |
|Adarkar Windform         |
|Admiral's Order          |
|Advanced Hoverguard      |
|Advanced Stitchwing      |
|Adverse Conditions       |
|Advice from the Fae      |
+-------------------------+
only showing top 20 rows



In [171]:
txtSql = "SELECT * FROM (SELECT count(colorIdentity) as NB, 'Black' as Color FROM AllCards WHERE colorIdentity LIKE '%B%'"
txtSql += "UNION SELECT count(colorIdentity) as NB, 'Green' as Color FROM AllCards WHERE colorIdentity LIKE '%G%'"
txtSql += "UNION SELECT count(colorIdentity) as NB, 'White' as Color FROM AllCards WHERE colorIdentity LIKE '%W%'"
txtSql += "UNION SELECT count(colorIdentity) as NB, 'Red' as Color FROM AllCards WHERE colorIdentity LIKE '%R%'"
txtSql += "UNION SELECT count(colorIdentity) as NB, 'Blue' as Color FROM AllCards WHERE colorIdentity LIKE '%U%'"
txtSql += "UNION SELECT count(colorIdentity) as NB, 'None' as Color FROM AllCards WHERE colorIdentity LIKE '[]') ORDER BY NB"
proto = AllCardsSqlContext.sql(txtSql)
proto.show(truncate = False)
# il y a un léger favoritisme pour le noir

+----+-----+
|NB  |Color|
+----+-----+
|2289|None |
|4370|Green|
|4390|Blue |
|4407|White|
|4423|Red  |
|4463|Black|
+----+-----+



In [126]:
proto = AllCardsDj[['legalities']].groupby(['legalities']).count()
proto.show(truncate = False)

+--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+-----+
|legalities                                                                                                                                                                      |count|
+--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+-----+
|{'commander': 'Banned', 'duel': 'Legal', 'legacy': 'Legal', 'modern': 'Legal', 'vintage': 'Legal'}                                                                              |8    |
|{'commander': 'Legal', 'duel': 'Legal', 'legacy': 'Legal', 'modern': 'Legal', 'pioneer': 'Legal', 'vintage': 'Legal'}                                                           |2150 |
|{'commander': 'Legal', 'duel': 'Legal', 'legacy': 'Legal', 'penny': 'Legal

In [131]:
proto = AllCardsSqlContext.sql("SELECT count(convertedManaCost) as NB, convertedManaCost FROM AllCards GROUP BY convertedManaCost ORDER BY convertedManaCost")
proto.show(truncate = False)

+----+-----------------+
|NB  |convertedManaCost|
+----+-----------------+
|1149|0.0              |
|1   |0.5              |
|2199|1.0              |
|4133|2.0              |
|4706|3.0              |
|3837|4.0              |
|2418|5.0              |
|1358|6.0              |
|572 |7.0              |
|214 |8.0              |
|75  |9.0              |
|35  |10.0             |
|13  |11.0             |
|6   |12.0             |
|6   |13.0             |
|1   |14.0             |
|5   |15.0             |
|1   |16.0             |
|1   |1000000.0        |
+----+-----------------+



In [137]:
proto = AllCardsSqlContext.sql("SELECT name, convertedManaCost FROM AllCards WHERE convertedManaCost IN(1000000,16,0.5)")
proto.show(truncate = False)
#Little girl fait référence à la plus jeune joueuse de magic

+-----------+-----------------+
|name       |convertedManaCost|
+-----------+-----------------+
|Draco      |16.0             |
|Gleemax    |1000000.0        |
|Little Girl|0.5              |
+-----------+-----------------+



In [152]:
# quel carte a la plus haute toughness ?
proto = AllCardsSqlContext.sql("SELECT MIN(name), COUNT(toughness) as NBtough, toughness FROM AllCards GROUP BY toughness ORDER BY NBtough,toughness")
proto.show(n=10000, truncate = False)
#les nan étant en grande partie des cartes non viable nous allons chercher à revenir sur les cartes viable avant de retourner sur la recherche de la carte la plus efficiente d'après le critère:
# Force + toughness - (MAX(convertedManaCost) - convertedManaCost)

+------------------------------+-------+---------+
|min(name)                     |NBtough|toughness|
+------------------------------+-------+---------+
|Chimney Goyf                  |1      |*+1      |
|S.N.O.T.                      |1      |*²       |
|Ninja                         |1      |+0       |
|Half-Squirrel, Half-          |1      |-0       |
|Spinal Parasite               |1      |-1       |
|Little Girl                   |1      |.5       |
|Fraction Jackson              |1      |1.5      |
|Autochthon Wurm               |1      |14       |
|Impervious Greatwurm          |1      |16       |
|Vile Bile                     |1      |2.5      |
|Kharis & The Beholder         |1      |20       |
|Shapeshifter                  |1      |7-*      |
|B.F.M. (Big Furry Monster) (b)|1      |99       |
|Half-Orc, Half-               |2      |+1       |
|Emrakul, the Aeons Torn       |2      |15       |
|Angry Mob                     |2      |2+*      |
|Loopy Lobster                 

In [175]:
# On va définir les cartes viable comme étant les cartes modernes Legal
proto = AllCardsSqlContext.sql("SELECT count(legalities) as NB, legalities FROM AllCards WHERE legalities LIKE  \"%'modern': 'Legal'%\"   GROUP BY legalities")
proto.show(truncate=False)

+----+-----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+
|NB  |legalities                                                                                                                                                                                           |
+----+-----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+
|8   |{'commander': 'Banned', 'duel': 'Legal', 'legacy': 'Legal', 'modern': 'Legal', 'vintage': 'Legal'}                                                                                                   |
|2150|{'commander': 'Legal', 'duel': 'Legal', 'legacy': 'Legal', 'modern': 'Legal', 'pioneer': 'Legal', 'vintage': 'Legal'}                                                         

In [189]:
#On commence pour voir si le noir est toujours favoriser
txtSql = "SELECT NB, Color FROM (SELECT count(colorIdentity) as NB, 'Black' as Color, COUNT(legalities) FROM AllCards WHERE colorIdentity LIKE '%B%' AND legalities LIKE  \"%'modern': 'Legal'%\" "
txtSql += "UNION SELECT count(colorIdentity) as NB, 'Green' as Color, COUNT(legalities) FROM AllCards WHERE colorIdentity LIKE '%G%' AND legalities LIKE  \"%'modern': 'Legal'%\" "
txtSql += "UNION SELECT count(colorIdentity) as NB, 'White' as Color, COUNT(legalities) FROM AllCards WHERE colorIdentity LIKE '%W%' AND legalities LIKE  \"%'modern': 'Legal'%\" "
txtSql += "UNION SELECT count(colorIdentity) as NB, 'Red' as Color, COUNT(legalities) FROM AllCards WHERE colorIdentity LIKE '%R%' AND legalities LIKE  \"%'modern': 'Legal'%\" "
txtSql += "UNION SELECT count(colorIdentity) as NB, 'Blue' as Color, COUNT(legalities) FROM AllCards WHERE colorIdentity LIKE '%U%' AND legalities LIKE  \"%'modern': 'Legal'%\" "
txtSql += "UNION SELECT count(colorIdentity) as NB, 'None' as Color, COUNT(legalities) FROM AllCards WHERE colorIdentity LIKE '[]' AND legalities LIKE  \"%'modern': 'Legal'%\") ORDER BY NB"
proto = AllCardsSqlContext.sql(txtSql)
proto.show(truncate = False)
# il y a un léger favoritisme pour le noir
# 3031 contre 4463


+----+-----+
|NB  |Color|
+----+-----+
|1264|None |
|2987|Blue |
|2990|Green|
|3016|White|
|3019|Red  |
|3031|Black|
+----+-----+



In [177]:
# On redémarre notre recherche de la carte la plus efficiente
proto = AllCardsSqlContext.sql("SELECT MIN(name), COUNT(toughness) as NBtough, toughness FROM AllCards WHERE legalities LIKE  \"%'modern': 'Legal'%\" GROUP BY toughness ORDER BY NBtough,toughness")
proto.show(truncate=False)

+-----------------------+-------+---------+
|min(name)              |NBtough|toughness|
+-----------------------+-------+---------+
|Spinal Parasite        |1      |-1       |
|Autochthon Wurm        |1      |14       |
|Impervious Greatwurm   |1      |16       |
|Emrakul, the Aeons Torn|2      |15       |
|Allosaurus Rider       |3      |1+*      |
|Ghalta, Primal Hunger  |4      |12       |
|Blightsteel Colossus   |7      |11       |
|Death's Shadow         |7      |13       |
|Bearer of the Heavens  |18     |10       |
|Ancient Brontodon      |20     |9        |
|Aggressive Mammoth     |54     |8        |
|Abominable Treefolk    |82     |*        |
|Altered Ego            |108    |0        |
|Accomplished Automaton |121    |7        |
|Abhorrent Overlord     |301    |6        |
|Abolisher of Bloodlines|586    |5        |
|Abomination of Gudul   |1037   |4        |
|Absolver Thrull        |1563   |3        |
|Abbot of Keral Keep    |1674   |1        |
|Abattoir Ghoul         |1935   